***
# Pattern Recognition Program
***

### **Improting Data**

In [34]:
import pandas as pd
#df = pd.read_csv("C:/Users/murma/Downloads/CENER.csv")
#df = pd.read_csv("C:/Users/murma/Downloads/DAT_MT_EURUSD_M1_202408.csv")
#df = pd.read_csv("C:/Users/murma/Downloads/EURUSD=X.csv")
df = pd.read_csv("C:/Users/murma/Downloads/META.csv")



### df=df[df['volume']!=0]
#df.rename(columns={'Ημερομ.': 'date', 'Υψηλό': 'high','Χαμηλό': 'low','Άνοιγμα': 'open','Κλείσιμο': 'close','Όγκος': 'volume'}, inplace=True)
#df.columns=['date','time', 'open', 'high', 'low', 'close', 'volume']
df.rename(columns={'Date':'date','Open':'open','High':'high','Low':'low','Close':'close','Adj Close':'adj close','Volume':'volume'},inplace=True)

#df['datetime'] = pd.to_datetime(df['date'] + ' ' + df['time'])

df.reset_index(drop=True, inplace=True)

#Check if NA values are in data
#df=df[df['volume']!=0]
df.isna().sum()

df.head(10)


date   open   high    low  close     volume
0  5/18/2012 16:00:00  42.00  45.00  38.00  38.23  580587712
1  5/21/2012 16:00:00  36.66  36.66  33.00  34.03  168309824
2  5/22/2012 16:00:00  32.59  33.59  30.94  31.00  102053824
3  5/23/2012 16:00:00  31.38  32.50  31.36  32.00   73721136
4  5/24/2012 16:00:00  32.98  33.21  31.77  33.03   50275880
5  5/25/2012 16:00:00  32.91  32.95  31.11  31.91   37189632
6  5/29/2012 16:00:00  31.48  31.69  28.65  28.84   78060800
7  5/30/2012 16:00:00  28.70  29.55  27.86  28.19   57267868
8  5/31/2012 16:00:00  28.54  29.67  26.83  29.60  111639200
9   6/1/2012 16:00:00  28.93  29.15  27.39  27.72   41855500

### **Defining Pivot Point Functions**

In [35]:
import numpy as np

def pivotid(df1, l, n1, n2): #n1 n2 before and after candle l
    if l-n1 < 0 or l+n2 >= len(df1):
        return 0
    
    pividlow=1
    pividhigh=1
    for i in range(l-n1, l+n2+1):
        if(df1.low[l]>df1.low[i]):
            pividlow=0
        if(df1.high[l]<df1.high[i]):
            pividhigh=0
    if pividlow and pividhigh:
        return 3
    elif pividlow:
        return 1
    elif pividhigh:
        return 2
    else:
        return 0
    
df['pivot'] = df.apply(lambda x: pivotid(df, x.name,5,5), axis=1)


def pointpos(x):
    if x['pivot']==1:
        return x['low']-1e-3
    elif x['pivot']==2:
        return x['high']+1e-3
    else:
        return np.nan

df['pointpos'] = df.apply(lambda row: pointpos(row), axis=1)

### **Defining Graph Functions**

In [36]:
import pandas as pd
import plotly.graph_objects as go
from plotly.subplots import make_subplots
import numpy as np
from matplotlib import pyplot
from scipy.stats import linregress


def graph_2(pattern, id, backcandles, xxmin, minim, xxmax, maxim):
    candleid = id

    slmin, intercmin, rmin, pmin, semin = linregress(xxmin, minim)
    slmax, intercmax, rmax, pmax, semax = linregress(xxmax, maxim)

    dfpl = df[candleid-backcandles-30:candleid+backcandles+10]

    # Create subplots and mention plot grid size
    fig = make_subplots(rows=2, cols=1, shared_xaxes=True, 
                vertical_spacing=0.01, subplot_titles=('OHLC', 'Volume'), 
                row_width=[0.5, 1.5])

    # Plot OHLC on 1st row
    fig.add_trace(go.Candlestick(x=dfpl.index, open=dfpl['open'],high=dfpl['high'],low=dfpl['low'],close=dfpl['close']), 
                    row=1, col=1
    )

    fig.add_scatter(x=dfpl.index, y=dfpl['pointpos'], mode="markers",
                            marker=dict(size=8, color="MediumPurple"),
                            name="pivot")

    # Bar trace for volumes on 2nd row without legend
    fig.add_trace(go.Bar(x=dfpl.index, y=dfpl['volume'], showlegend=False,), row=2, col=1)

    xxmin = np.append(xxmin, xxmin[-1]+15)
    xxmax = np.append(xxmax, xxmax[-1]+15)

    fig.add_trace(go.Scatter(x=xxmin, y=slmin*xxmin + intercmin, mode='lines', name='min slope'))
    fig.add_trace(go.Scatter(x=xxmax, y=slmax*xxmax + intercmax, mode='lines', name='max slope'))

    # Do not show OHLC's rangeslider plot 
    fig.update(layout_xaxis_rangeslider_visible=False)
    fig.show()

def graph(pattern, id, backcandles, xxmin, minim, xxmax, maxim):

    if pattern == 'triangle' or pattern == 'head_and_shoulders' or pattern == 'inverted_head_and_shoulders' or pattern == 'double_top' or pattern == 'double_bottom' or pattern == 'wedge' or pattern=='channel':

        graph_2(pattern, id, backcandles, xxmin, minim, xxmax, maxim)

    if pattern == 'uptrend' or pattern =='support':
        
        candleid = id

        slmin, intercmin, rmin, pmin, semin = linregress(xxmin, minim)

        dfpl = df[candleid-backcandles-30:candleid+backcandles+10]

        # Create subplots and mention plot grid size
        fig = make_subplots(rows=2, cols=1, shared_xaxes=True, 
                    vertical_spacing=0.01, subplot_titles=('OHLC', 'Volume'), 
                    row_width=[0.5, 1.5])

        # Plot OHLC on 1st row
        fig.add_trace(go.Candlestick(x=dfpl.index, open=dfpl['open'],high=dfpl['high'],low=dfpl['low'],close=dfpl['close']), 
                        row=1, col=1
        )

        fig.add_scatter(x=dfpl.index, y=dfpl['pointpos'], mode="markers",
                                marker=dict(size=8, color="MediumPurple"),
                                name="pivot")

        # Bar trace for volumes on 2nd row without legend
        fig.add_trace(go.Bar(x=dfpl.index, y=dfpl['volume'], showlegend=False), row=2, col=1)

        xxmin = np.append(xxmin, xxmin[-1]+15)

        fig.add_trace(go.Scatter(x=xxmin, y=slmin*xxmin + intercmin, mode='lines', name='min slope'))

        # Do not show OHLC's rangeslider plot 
        fig.update(layout_xaxis_rangeslider_visible=False)
        fig.show()

    if pattern == 'downtrend' or pattern == 'resistance':
                
        candleid = id

        slmax, intercmax, rmax, pmax, semax = linregress(xxmax, maxim)

        dfpl = df[candleid-backcandles-30:candleid+backcandles+10]

        # Create subplots and mention plot grid size
        fig = make_subplots(rows=2, cols=1, shared_xaxes=True, 
                    vertical_spacing=0.01, subplot_titles=('OHLC', 'Volume'), 
                    row_width=[0.5, 1.5])

        # Plot OHLC on 1st row
        fig.add_trace(go.Candlestick(x=dfpl.index, open=dfpl['open'],high=dfpl['high'],low=dfpl['low'],close=dfpl['close']), 
                        row=1, col=1
        )

        fig.add_scatter(x=dfpl.index, y=dfpl['pointpos'], mode="markers",
                                marker=dict(size=8, color="MediumPurple"),
                                name="pivot")

        # Bar trace for volumes on 2nd row without legend
        fig.add_trace(go.Bar(x=dfpl.index, y=dfpl['volume'], showlegend=False), row=2, col=1)

        xxmax = np.append(xxmax, xxmax[-1]+15)

        fig.add_trace(go.Scatter(x=xxmax, y=slmax*xxmax + intercmax, mode='lines', name='max slope'))

        # Do not show OHLC's rangeslider plot 
        fig.update(layout_xaxis_rangeslider_visible=False)
        fig.show()


### **Triangle**

In [37]:
import numpy as np
from matplotlib import pyplot
from scipy.stats import linregress

backcandles = 30
d=3

df['pivot'] = df.apply(lambda x: pivotid(df, x.name,d,d), axis=1)

df['pointpos'] = df.apply(lambda row: pointpos(row), axis=1)

repeat_array=np.array([])

for candleid in range(len(df)):
    maxim = np.array([])
    minim = np.array([])
    xxmin = np.array([])
    xxmax = np.array([])
    
    for i in range(candleid-backcandles, candleid+1):
        if df.iloc[i].pivot == 1:
            minim = np.append(minim, df.iloc[i].low)
            xxmin = np.append(xxmin, i) 
        if df.iloc[i].pivot == 2:
            maxim = np.append(maxim, df.iloc[i].high)
            xxmax = np.append(xxmax, i) 
    if (xxmax.size <3 and xxmin.size <3) or xxmax.size==0 or xxmin.size==0:
        continue
       
    if xxmax[0] not in  repeat_array and xxmin[0] not in repeat_array:

        slmin, intercmin, rmin, pmin, semin = linregress(xxmin, minim)
        slmax, intercmax, rmax, pmax, semax = linregress(xxmax, maxim)
 
        if abs(rmax)>=0.8 and abs(rmin)>=0.8 and abs(slmax)<=0.20 and slmin>0.20 and slmax<=0:

            repeat_array=np.append(repeat_array,xxmax[0])
            repeat_array=np.append(repeat_array,xxmin[0])

            print('ASCENDING TRIANGLE', candleid, backcandles, d)

            graph('triangle',candleid,backcandles,xxmin, minim, xxmax, maxim)
        elif abs(rmax)>=0.8 and abs(rmin)>=0.8 and abs(slmin)<=0.20 and slmax<-0.20 and slmin>=0:

            repeat_array=np.append(repeat_array,xxmax[0])
            repeat_array=np.append(repeat_array,xxmin[0])

            print('DESCENDING TRIANGLE', candleid, backcandles, d)

            graph('triangle',candleid,backcandles,xxmin, minim, xxmax, maxim)

        elif abs(rmax)>=0.8 and abs(rmin)>=0.8 and ((slmax<=-0.20 and slmin>=0.20) or (slmax>=-0.20 and slmin<=0.20 and slmax<0 and slmin>0)):

            repeat_array=np.append(repeat_array,xxmax[0])
            repeat_array=np.append(repeat_array,xxmin[0])

            print('SYMMETRICAL TRIANGLE', candleid, backcandles, d)

            graph('triangle',candleid,backcandles,xxmin, minim, xxmax, maxim)






SYMMETRICAL TRIANGLE 100 30 3


C:\Users\murma\AppData\Local\Packages\PythonSoftwareFoundation.Python.3.12_qbz5n2kfra8p0\LocalCache\local-packages\Python312\site-packages\scipy\stats\_stats_py.py:10919: RuntimeWarning:

invalid value encountered in scalar divide

C:\Users\murma\AppData\Local\Packages\PythonSoftwareFoundation.Python.3.12_qbz5n2kfra8p0\LocalCache\local-packages\Python312\site-packages\scipy\stats\_stats_py.py:10933: RuntimeWarning:

invalid value encountered in sqrt

C:\Users\murma\AppData\Local\Packages\PythonSoftwareFoundation.Python.3.12_qbz5n2kfra8p0\LocalCache\local-packages\Python312\site-packages\scipy\stats\_stats_py.py:10936: RuntimeWarning:

invalid value encountered in scalar divide



DESCENDING TRIANGLE 627 30 3


ASCENDING TRIANGLE 816 30 3


SYMMETRICAL TRIANGLE 949 30 3


...

DESCENDING TRIANGLE 2587 30 3


DESCENDING TRIANGLE 2595 30 3


SYMMETRICAL TRIANGLE 2649 30 3


ASCENDING TRIANGLE 2672 30 3


SYMMETRICAL TRIANGLE 3015 30 3


### **Head and Shoulders**

In [38]:
import numpy as np
from matplotlib import pyplot
from scipy.stats import linregress

backcandles= 70
d=7

df['pivot'] = df.apply(lambda x: pivotid(df, x.name,d,d), axis=1)

df['pointpos'] = df.apply(lambda row: pointpos(row), axis=1)

repeatxxhead=np.array([])

for candleid in range(len(df)):
    maxim = np.array([])
    minim = np.array([])
    xxmin = np.array([])
    xxmax = np.array([])

    top_1=1
    xxtop_1=1

    head=0
    xxhead=0

    top_2=1
    xxtop_2=1

    z=0
    k=0
    h=0

    for i in range(candleid-backcandles, candleid+1):

        if df.iloc[i].pivot == 2:
            if df.iloc[i].high>top_1 :
                if df.iloc[i].high>head :
                    top_1=head
                    xxtop_1=xxhead
                    head=df.iloc[i].high
                    xxhead=i

                    z=z+1

                elif df.iloc[i].high>top_2 and i > xxhead :
                    top_2=df.iloc[i].high
                    xxtop_2=i
                    k=k+1
            
            elif df.iloc[i].high>top_2 and i > xxhead :
                top_2=df.iloc[i].high
                xxtop_2=i
                k=k+1

        if z>=2 and k>=1 :  
            range_1= range(int(xxtop_1),int(xxhead))
            
            range_2= range(int(xxhead),int(xxtop_2))

            bot_1=1000000
            xxbot_1=0

            bot_2=1000000
            xxbot_2=1

            for j in range_1:
                    if df.iloc[j].pivot == 1:

                        if df.iloc[j].low<bot_1 :
                            bot_1=df.iloc[j].low
                            xxbot_1= j
                            h=h+1

            for j in range_2:
                    if df.iloc[j].pivot == 1:

                        if df.iloc[j].low<bot_2 :
                            bot_2=df.iloc[j].low
                            xxbot_2= j
                            h=h+1

         
    if  df.iloc[i].close >  bot_2 or z<2 or k<1 or h <2:
        continue


    if xxhead not in repeatxxhead and xxbot_1 != xxbot_2 and xxhead > xxtop_1 and  xxhead < xxtop_2 and xxbot_2 != 1 and xxbot_1 !=0:
        repeatxxhead=np.append(repeatxxhead, xxhead)

        print(xxtop_1,xxtop_2)
        print(xxbot_1,xxbot_2)
        
        maxim = np.append(maxim, top_1)
        xxmax = np.append(xxmax, xxtop_1) 

        maxim = np.append(maxim, top_2)
        xxmax = np.append(xxmax, xxtop_2)

        minim = np.append(minim, bot_1)
        xxmin = np.append(xxmin, xxbot_1)

        minim = np.append(minim, bot_2)
        xxmin = np.append(xxmin, xxbot_2)


        slmin, intercmin, rmin, pmin, semin = linregress(xxmin, minim)
        slmax, intercmax, rmax, pmax, semax = linregress(xxmax, maxim)
            
        print( 'head_and_shoulders',candleid, backcandles, d)


        
        graph('double_top',candleid, backcandles,xxmin, minim,xxmax, maxim)
        
        
    

163 199
167 194
head_and_shoulders 208 70 7


701 735
705 722
head_and_shoulders 738 70 7


779 808
786 803
head_and_shoulders 818 70 7


1283 1337
1288 1328
head_and_shoulders 1346 70 7


1418 1461
1424 1441
head_and_shoulders 1469 70 7


1531 1564
1539 1558
head_and_shoulders 1585 70 7


1895 1950
1905 1937
head_and_shoulders 1952 70 7


2122 2149
2128 2143
head_and_shoulders 2172 70 7


2312 2371
2316 2365
head_and_shoulders 2375 70 7


2371 2418
2377 2402
head_and_shoulders 2438 70 7


### **Inverted Head and Shoulders**

In [39]:
import numpy as np
from matplotlib import pyplot
from scipy.stats import linregress

backcandles = 30
d = 3

df['pivot'] = df.apply(lambda x: pivotid(df, x.name, d, d), axis=1)
df['pointpos'] = df.apply(lambda row: pointpos(row), axis=1)

repeatxxhead = np.array([])

for candleid in range(backcandles,len(df)):
    maxim = np.array([])
    minim = np.array([])
    xxmin = np.array([])
    xxmax = np.array([])

    bot_1 = 1000000 
    xxbot_1 = 0

    head = 1000000 
    xxhead = 0

    bot_2 = 1000000 
    xxbot_2 = 1

    z = 0  
    k = 0  
    h = 0  

    for i in range(candleid - backcandles, candleid + 1):

        if df.iloc[i].pivot == 1:
            if df.iloc[i].low < bot_1:
                if df.iloc[i].low < head:

                    bot_1 = head
                    xxbot_1 = xxhead
                    head = df.iloc[i].low
                    xxhead = i
                    z += 1
                elif df.iloc[i].low < bot_2 and i > xxhead:

                    bot_2 = df.iloc[i].low
                    xxbot_2 = i
                    k += 1
            elif df.iloc[i].low < bot_2 and i > xxhead:
                bot_2 = df.iloc[i].low
                xxbot_2 = i
                k += 1

 
        if z >= 2 and k >= 1:  
            range_1 = range(int(xxbot_1), int(xxhead))
            range_2 = range(int(xxhead), int(xxbot_2))

            top_1 = -1 
            xxtop_1 = 1

            top_2 = -1  
            xxtop_2 = 1

            for j in range_1:
                if df.iloc[j].pivot == 2:
                    if df.iloc[j].high > top_1:
                        top_1 = df.iloc[j].high
                        xxtop_1 = j
                        h += 1

            for j in range_2:
                if df.iloc[j].pivot == 2:
                    if df.iloc[j].high > top_2:
                        top_2 = df.iloc[j].high
                        xxtop_2 = j
                        h += 1

    if df.iloc[i].close < top_2 or z < 2 or k < 1 or h < 2:
        continue


    if xxhead not in repeatxxhead and xxtop_1 != xxtop_2 and xxhead > xxbot_1 and xxhead < xxbot_2 and xxtop_1 != 1 and xxtop_2 != 1:
        repeatxxhead = np.append(repeatxxhead, xxhead)

        minim = np.append(minim, bot_1)
        xxmin = np.append(xxmin, xxbot_1)

        minim = np.append(minim, bot_2)
        xxmin = np.append(xxmin, xxbot_2)

        maxim = np.append(maxim, top_1)
        xxmax = np.append(xxmax, xxtop_1)

        maxim = np.append(maxim, top_2)
        xxmax = np.append(xxmax, xxtop_2)

        slmin, intercmin, rmin, pmin, semin = linregress(xxmin, minim)
        slmax, intercmax, rmax, pmax, semax = linregress(xxmax, maxim)

        print('inverted_head_and_shoulders',candleid, backcandles, d)

        graph('double_bottom', candleid, backcandles, xxmin, minim, xxmax, maxim)


inverted_head_and_shoulders 128 30 3


inverted_head_and_shoulders 277 30 3


inverted_head_and_shoulders 440 30 3


inverted_head_and_shoulders 506 30 3


inverted_head_and_shoulders 546 30 3


...

inverted_head_and_shoulders 2549 30 3


inverted_head_and_shoulders 2685 30 3


inverted_head_and_shoulders 2841 30 3


inverted_head_and_shoulders 3050 30 3


inverted_head_and_shoulders 3077 30 3


### **Double Top**

In [40]:
import numpy as np
from matplotlib import pyplot
from scipy.stats import linregress

backcandles = 90
d = 10

df['pivot'] = df.apply(lambda x: pivotid(df, x.name, d, d), axis=1)
df['pointpos'] = df.apply(lambda row: pointpos(row), axis=1)

for candleid in range(len(df)):
    minim = np.array([])  
    maxim = np.array([])  
    xxmin = np.array([])  
    xxmax = np.array([])  
    arrayxxdeep = np.array([])  
    deep = 10000  
    xxdeep = 0
    top_1 = -10000  
    top_2 = -10000  
    xxtop_1 = 1
    xxtop_2 = 0
    z = 0

    
    for i in range(candleid - backcandles, candleid + 1):
        condition_1 = False

       
        if df.iloc[i].pivot == 2:  
            if df.iloc[i].high > top_2:
                if df.iloc[i].high > top_1:
                    top_2 = top_1
                    xxtop_2 = xxtop_1
                    top_1 = df.iloc[i].high
                    xxtop_1 = i
                    z += 1
                else:
                    top_2 = df.iloc[i].high
                    xxtop_2 = i

      
        if xxtop_1 < xxtop_2:
            range_1 = range(int(xxtop_1), int(xxtop_2))
            
           
        else:
            range_1 = range(int(xxtop_2), int(xxtop_1))

        deep = 10000  
        xxdeep = 0

        if z >= 2:  
            for j in range_1:
                if df.iloc[j].pivot == 1:  
                    if df.iloc[j].low < deep:
                        deep = df.iloc[j].low
                        xxdeep = j

        
        if df.iloc[i].close <= deep:
            if xxdeep not in arrayxxdeep:
                condition_1 = True
                xxbreak = i
                arrayxxdeep = np.append(arrayxxdeep, xxdeep)
    
    if not condition_1:
        continue

   
    if xxtop_1 < xxtop_2:
        maxim = np.append(maxim, top_1)
        xxmax = np.append(xxmax, xxtop_1)

        maxim = np.append(maxim, top_2)
        xxmax = np.append(xxmax, xxtop_2)
    else:
        maxim = np.append(maxim, top_2)
        xxmax = np.append(xxmax, xxtop_2)

        maxim = np.append(maxim, top_1)
        xxmax = np.append(xxmax, xxtop_1)

    
    minim = np.append(minim, deep)
    xxmin = np.append(xxmin, xxdeep)

    minim = np.append(minim, df.iloc[i].close)
    xxmin = np.append(xxmin, i)

    
    slmin, intercmin, rmin, pmin, semin = linregress(xxmin, minim)
    slmax, intercmax, rmax, pmax, semax = linregress(xxmax, maxim)

    
    if abs(slmax) <= 0.1:  
        print('double_top',candleid, backcandles, d)

        
        graph('double_top', candleid, backcandles, xxmin, minim, xxmax, maxim)


double_top 0 90 10


double_top 211 90 10


double_top 602 90 10


double_top 1123 90 10


double_top 1346 90 10


double_top 2438 90 10


### **Double Bottom**

In [41]:
import numpy as np
from matplotlib import pyplot
from scipy.stats import linregress

backcandles= 90
d=10

df['pivot'] = df.apply(lambda x: pivotid(df, x.name,d,d), axis=1)
df['pointpos'] = df.apply(lambda row: pointpos(row), axis=1)

k=0
for candleid in range(len(df)):
    minim = np.array([])  
    maxim = np.array([]) 
    xxmin = np.array([])  
    xxmax = np.array([])  
    arrayxxpeak = np.array([])  
    peak = -10000  
    xxpeak = 0  
    bottom_1 = 10000
    bottom_2 = 10000
    xxbottom_1 = 1
    xxbottom_2 = 0
    z = 0


    for i in range(candleid-backcandles, candleid+1):
        condition_1 = False

        if df.iloc[i].pivot == 1:  
            if df.iloc[i].low < bottom_2:
                if df.iloc[i].low < bottom_1:
                    bottom_2 = bottom_1
                    xxbottom_2 = xxbottom_1
                    bottom_1 = df.iloc[i].low
                    xxbottom_1 = i
                    z = z + 1
                    
                else:
                    bottom_2 = df.iloc[i].low
                    xxbottom_2 = i

        if xxbottom_1 < xxbottom_2:
            range_1 = range(int(xxbottom_1), int(xxbottom_2))
            
        else:
            range_1 = range(int(xxbottom_2), int(xxbottom_1))

        peak = -10000  
        xxpeak = 0  

        if z >= 2:  
            for j in range_1:
                if df.iloc[j].pivot == 2:  
                    if df.iloc[j].high > peak:  
                        peak = df.iloc[j].high  
                        xxpeak = j  

        
        if df.iloc[i].close >= peak:  
            if xxpeak not in arrayxxpeak:  
                condition_1 = True
                xxbreak = i
                arrayxxpeak = np.append(arrayxxpeak, xxpeak) 

    if not condition_1:
        continue

    
    if xxbottom_1 < xxbottom_2:
        minim = np.append(minim, bottom_1)
        xxmin = np.append(xxmin, xxbottom_1)

        minim = np.append(minim, bottom_2)
        xxmin = np.append(xxmin, xxbottom_2)
    else:
        minim = np.append(minim, bottom_2)
        xxmin = np.append(xxmin, xxbottom_2)

        minim = np.append(minim, bottom_1)
        xxmin = np.append(xxmin, xxbottom_1)

    xxmax = np.array([])
    maxim = np.array([])

    maxim = np.append(maxim, peak)  
    xxmax = np.append(xxmax, xxpeak)  

    maxim = np.append(maxim, df.iloc[i].close)
    xxmax = np.append(xxmax, i)

    
    slmin, intercmin, rmin, pmin, semin = linregress(xxmin, minim)
    slmax, intercmax, rmax, pmax, semax = linregress(xxmax, maxim)

    
    if abs(slmin) <= 0.1:
        print('double_bottom',candleid, backcandles, d)  
        
        print(slmin)

        graph('double_bottom', candleid, backcandles, xxmin, minim, xxmax, maxim)


double_bottom 296 90 10
-0.04183673469387749


double_bottom 652 90 10
0.08423076923076969


double_bottom 777 90 10
-0.010930232558139508


### **Wedge**

In [42]:
import numpy as np
from matplotlib import pyplot
from scipy.stats import linregress

backcandles= 30
d=3


repeat_array=np.array([])

df['pivot'] = df.apply(lambda x: pivotid(df, x.name,d,d), axis=1)

df['pointpos'] = df.apply(lambda row: pointpos(row), axis=1)

for candleid in range(len(df)):
    maxim = np.array([])
    minim = np.array([])
    xxmin = np.array([])
    xxmax = np.array([])
    for i in range(candleid-backcandles, candleid+1):
        if df.iloc[i].pivot == 1:
            minim = np.append(minim, df.iloc[i].low)
            xxmin = np.append(xxmin, i) 
        if df.iloc[i].pivot == 2:
            maxim = np.append(maxim, df.iloc[i].high)
            xxmax = np.append(xxmax, i)
    
    if (xxmax.size <3 or xxmin.size <3) or xxmax.size==0 or xxmin.size==0:
        continue

    if xxmax[0] not in  repeat_array and xxmin[0] not in repeat_array:
    

        slmin, intercmin, rmin, pmin, semin = linregress(xxmin, minim)
        slmax, intercmax, rmax, pmax, semax = linregress(xxmax, maxim)
                
        if abs(rmax)>=0.9 and abs(rmin)>=0.9 and ((slmax>=0.001 and (slmin>=slmax+0.01)) or (slmin<=-0.001 and (slmin-0.01>=slmax))) :
            
            if slmax>=0.001 and slmin>=slmax+0.001:

                repeat_array=np.append(repeat_array,xxmax[0])
                repeat_array=np.append(repeat_array,xxmin[0])

                print(rmin, rmax, candleid, xxmax, xxmin)
                print('rising wedge',candleid, backcandles, d)
                graph('wedge',candleid,backcandles,xxmin, minim, xxmax, maxim)
            
            if slmin<=-0.001 and slmin-0.001>=slmax:
                repeat_array=np.append(repeat_array,xxmax[0])
                repeat_array=np.append(repeat_array,xxmin[0])

                print('falling wedge',candleid, backcandles, d)
                graph('wedge',candleid,backcandles,xxmin, minim, xxmax, maxim)


            


falling wedge 64 30 3


falling wedge 74 30 3


falling wedge 107 30 3


falling wedge 199 30 3


0.9790711226306458 0.9103731948237825 292 [264. 271. 279. 290.] [262. 268. 274. 281. 292.]
rising wedge 292 30 3


...

0.9753854473782412 0.9074422882415332 2959 [2931. 2945. 2954. 2959.] [2933. 2943. 2952. 2957.]
rising wedge 2959 30 3


0.9613427674350034 0.9315658565817282 2964 [2945. 2954. 2959.] [2943. 2952. 2957.]
rising wedge 2964 30 3


0.9076763662068879 0.9436969790655444 3046 [3016. 3024. 3035. 3045.] [3022. 3027. 3041.]
rising wedge 3046 30 3


0.9613281032163133 0.935354455117651 3055 [3035. 3045. 3051.] [3027. 3041. 3047.]
rising wedge 3055 30 3


0.9462036078101792 0.938620748318287 3089 [3062. 3069. 3079. 3084.] [3064. 3071. 3081.]
rising wedge 3089 30 3


### **Channel**

In [43]:
import numpy as np
from matplotlib import pyplot
from scipy.stats import linregress

backcandles= 60
d=3
repeat_array=np.array([])


df['pivot'] = df.apply(lambda x: pivotid(df, x.name,d,d), axis=1)

df['pointpos'] = df.apply(lambda row: pointpos(row), axis=1)

for candleid in range(len(df)):
    maxim = np.array([])
    minim = np.array([])
    xxmin = np.array([])
    xxmax = np.array([])
    for i in range(candleid-backcandles, candleid):
        if df.iloc[i].pivot == 1:
            minim = np.append(minim, df.iloc[i].low)
            xxmin = np.append(xxmin, i) 
        if df.iloc[i].pivot == 2:
            maxim = np.append(maxim, df.iloc[i].high)
            xxmax = np.append(xxmax, i) 
    
    if (xxmax.size <3 or xxmin.size <3) or xxmax.size==0 or xxmin.size==0 :
        continue




    if xxmax[0] not in  repeat_array and xxmin[0] not in repeat_array:

        slmin, intercmin, rmin, pmin, semin = linregress(xxmin, minim)
        slmax, intercmax, rmax, pmax, semax = linregress(xxmax, maxim)
        if abs(rmax)>=0.9 and abs(rmin)>=0.9 and ((slmax<=slmin*1.20 and slmax>=slmin*0.80) or (slmax>=slmin*1.20 and slmax<=slmin*0.80)) :
            if slmax>0 :   
                repeat_array=np.append(repeat_array,xxmax)
                repeat_array=np.append(repeat_array,xxmin) 

                print('ascending channel',candleid, backcandles, d)
                graph('channel',i,backcandles,xxmin, minim, xxmax, maxim)

            elif slmax<0 :
                repeat_array=np.append(repeat_array,xxmax)
                repeat_array=np.append(repeat_array,xxmin)

                print('descending channel',candleid, backcandles, d)
                graph('channel',i,backcandles,xxmin, minim, xxmax, maxim)


descending channel 73 60 3


ascending channel 164 60 3


ascending channel 329 60 3


ascending channel 443 60 3


ascending channel 566 60 3


...

ascending channel 2314 60 3


descending channel 2625 60 3


ascending channel 2761 60 3


ascending channel 2820 60 3


ascending channel 2955 60 3


### **Uptrend / Downtrend**


In [44]:
import numpy as np
from matplotlib import pyplot
from scipy.stats import linregress

backcandles= 30
d=3

df['pivot'] = df.apply(lambda x: pivotid(df, x.name,d,d), axis=1)

df['pointpos'] = df.apply(lambda row: pointpos(row), axis=1)

resarray = np.array([])

suparray = np.array([])

for candleid in range(len(df)):
    
    maxim = np.array([])
    minim = np.array([])
    xxmin = np.array([])
    xxmax = np.array([])
    for i in range(candleid-backcandles, candleid+1):
        if df.iloc[i].pivot == 1:
            minim = np.append(minim, df.iloc[i].low)
            xxmin = np.append(xxmin, i) 
        if df.iloc[i].pivot == 2:
            maxim = np.append(maxim, df.iloc[i].high)
            xxmax = np.append(xxmax, i) 
    
    if (xxmax.size <3 and xxmin.size <3) :
        continue

    if i in xxmin and xxmin[0] not in suparray:
        slmin, intercmin, rmin, pmin, semin = linregress(xxmin, minim)
        if (abs(rmin)>=0.90 and slmin>=0.10):
            print('uptrend',candleid, backcandles, d)

            graph('uptrend',candleid ,backcandles, xxmin, minim, xxmax, maxim)
            suparray = np.append(suparray, xxmin)

    if i in xxmax and xxmax[0] not in resarray:
        slmax, intercmax, rmax, pmax, semax = linregress(xxmax, maxim)
        if (abs(rmax)>=0.90 and slmax<=-0.10):
            print('downtrend',candleid, backcandles, d)

            graph('downtrend',candleid ,backcandles, xxmin, minim, xxmax, maxim)
            resarray = np.append(resarray, xxmax)

        

downtrend 46 30 3


downtrend 105 30 3


downtrend 199 30 3


downtrend 264 30 3


uptrend 311 30 3


...

uptrend 2933 30 3


uptrend 2976 30 3


uptrend 3015 30 3


downtrend 3016 30 3


uptrend 3047 30 3


### **Support / Resistance**

In [45]:
import numpy as np
from matplotlib import pyplot
from scipy.stats import linregress

backcandles= 30
d=3

df['pivot'] = df.apply(lambda x: pivotid(df, x.name,d,d), axis=1)

df['pointpos'] = df.apply(lambda row: pointpos(row), axis=1)

resarray = np.array([])

suparray = np.array([])

for candleid in range(len(df)):
    
    maxim = np.array([])
    minim = np.array([])
    xxmin = np.array([])
    xxmax = np.array([])
    for i in range(candleid-backcandles, candleid+1):
        if df.iloc[i].pivot == 1:
            minim = np.append(minim, df.iloc[i].low)
            xxmin = np.append(xxmin, i) 
        if df.iloc[i].pivot == 2:
            maxim = np.append(maxim, df.iloc[i].high)
            xxmax = np.append(xxmax, i) 
    
    if (xxmax.size <3 or xxmin.size <3) :
        continue

    if i in xxmin and xxmin[0] not in suparray :
        slmin, intercmin, rmin, pmin, semin = linregress(xxmin, minim)

        if (abs(rmin)>=0.80 and abs(slmin)<=0.10):
            
            print('SUPPORT',candleid, backcandles, d)

            graph('support',candleid ,backcandles, xxmin, minim, xxmax, maxim)
            suparray = np.append(suparray, xxmin[1])

    if i in xxmax and xxmax[0] not in resarray:
        slmax, intercmax, rmax, pmax, semax = linregress(xxmax, maxim)
        if (abs(rmax)>=0.80 and abs(slmax)<=0.10):
            print('RESISTANCE',candleid, backcandles, d)

            graph('resistance',candleid ,backcandles, xxmin, minim, xxmax, maxim)
            resarray = np.append(resarray, xxmax[1])



        

SUPPORT 107 30 3


RESISTANCE 290 30 3


SUPPORT 292 30 3


SUPPORT 457 30 3


RESISTANCE 497 30 3


SUPPORT 661 30 3


RESISTANCE 908 30 3


SUPPORT 1108 30 3


SUPPORT 1322 30 3


SUPPORT 2592 30 3


In [46]:
import numpy as np
from matplotlib import pyplot
from scipy.stats import linregress

backcandles= 30
d=3

df['pivot'] = df.apply(lambda x: pivotid(df, x.name,d,d), axis=1)

df['pointpos'] = df.apply(lambda row: pointpos(row), axis=1)

resarray = np.array([])

suparray = np.array([])

for candleid in range(len(df)):
    
    maxim = np.array([])
    minim = np.array([])
    xxmin = np.array([])
    xxmax = np.array([])
    for i in range(candleid-backcandles, candleid+1):
        if df.iloc[i].pivot == 1:
            minim = np.append(minim, df.iloc[i].low)
            xxmin = np.append(xxmin, i) 
        if df.iloc[i].pivot == 2:
            maxim = np.append(maxim, df.iloc[i].high)
            xxmax = np.append(xxmax, i) 
    
    if (xxmax.size <3 or xxmin.size <3) :
        continue

    if i in xxmin and xxmin[0] not in suparray :
        slmin, intercmin, rmin, pmin, semin = linregress(xxmin, minim)

        if (abs(rmin)>=0.80 and abs(slmin)<=0.10):
            
            print('SUPPORT',candleid, backcandles, d)

            graph('support',candleid ,backcandles, xxmin, minim, xxmax, maxim)
            suparray = np.append(suparray, xxmin[1])

    if i in xxmax and xxmax[0] not in resarray:
        slmax, intercmax, rmax, pmax, semax = linregress(xxmax, maxim)
        if (abs(rmax)>=0.80 and abs(slmax)<=0.10):
            print('RESISTANCE',candleid, backcandles, d)

            graph('resistance',candleid ,backcandles, xxmin, minim, xxmax, maxim)
            resarray = np.append(resarray, xxmax[1])



        

SUPPORT 107 30 3


RESISTANCE 290 30 3


SUPPORT 292 30 3


SUPPORT 457 30 3


RESISTANCE 497 30 3


SUPPORT 661 30 3


RESISTANCE 908 30 3


SUPPORT 1108 30 3


SUPPORT 1322 30 3


SUPPORT 2592 30 3
